In [2]:
from pandas import read_csv
from matplotlib import pyplot
import sys
import numpy as np
import pandas as pd
from datetime import datetime


#DATOS PISOA
flat="./pisoA/"
day="19244"
folders=["TRACK2","TRACK3","TRACK4","TRACK5","TRACK6","TRACK7","TRACK8","TRACK9"]

#DATOS PISOB
#flat="./pisoB/"
#day="19311"
#folders=["TRACK1","TRACK2","TRACK3","TRACK4","TRACK5","TRACK6","TRACK7","TRACK8","TRACK9"]


#Ventanas temporales de valores "pasados" (los datos RSSI despues de la estimación de tiempo) hasta 12 segundos
tW1=[0,-1,-2,-3,-4,-6,-8,-10,-12]





#LEEMOS los datos RSSI (tiempo, ancla y señal)
data=[]
N=0
for f in folders:
    series=read_csv(flat+f+"/uwb/"+day+".rssi.1.tsv", sep="\t",parse_dates=True,header=None)
    N=N+len(series.values)
    d2=series.values
    d2=np.array(d2)
    print(d2)
    print(d2[:,2])
    data.extend(d2)

data=np.array(data)
print(len(data))
print(N)


[[1662734448 '2022-09-09 16:40:48' 8139 -81.38]
 [1662734448 '2022-09-09 16:40:48' 28079 -81.4]
 [1662734448 '2022-09-09 16:40:48' 31176 -89.19]
 ...
 [1662734886 '2022-09-09 16:48:06' 28079 -80.32]
 [1662734886 '2022-09-09 16:48:06' 31176 -89.35]
 [1662734886 '2022-09-09 16:48:06' 38719 -85.69]]
[8139 28079 31176 ... 28079 31176 38719]
[[1662735015 '2022-09-09 16:50:15' 8139 -84.49]
 [1662735015 '2022-09-09 16:50:15' 28079 -81.04]
 [1662735015 '2022-09-09 16:50:15' 31176 -87.59]
 ...
 [1662735557 '2022-09-09 16:59:17' 28079 -80.38]
 [1662735557 '2022-09-09 16:59:17' 31176 -85.71]
 [1662735557 '2022-09-09 16:59:17' 38719 -88.13]]
[8139 28079 31176 ... 28079 31176 38719]
[[1662735619 '2022-09-09 17:00:19' 8139 -84.74]
 [1662735619 '2022-09-09 17:00:19' 28079 -80.28]
 [1662735619 '2022-09-09 17:00:19' 31176 -90.62]
 ...
 [1662736106 '2022-09-09 17:08:26' 28079 -80.71]
 [1662736106 '2022-09-09 17:08:26' 31176 -86.64]
 [1662736106 '2022-09-09 17:08:26' 38719 -85.83]]
[8139 28079 31176 ... 

In [3]:
#Leemos los datos del ground truth que ha etiquetado el usuario (pixeles en la imagen)
dataY=[]

for f in folders:
    series=read_csv(flat+f+"/location_gt/"+day+".location.tsv", sep="\t",parse_dates=True,header=None)
    for d in series.values:
        dataY.append(d)
dataY=np.array(dataY)

In [4]:
#Leemos las diferentes anclas (4) que hay configuradas
print(data[:,2])
anchors=np.unique(data[:,2])
print(anchors)

[8139 28079 31176 ... 28079 31176 38719]
[8139 28079 31176 38719]


In [5]:
#Normalizamos los valores de RSSI
min_v=(float)(min(data[:,3]))
max_v=(float)(max(data[:,3]))
print(min_v,max_v)

-120.0 -78.81


In [6]:
#INFO: tiempo inicial y final de los datos
min_t=(float)(min(dataY[:,0]))
max_t=(float)(max(dataY[:,0]))
print(min_t,max_t)

1662734464.0 1662740468.0


In [7]:
#INFO: valores min max de la Y
min_y=(float)(min(dataY[:,4]))
max_y=(float)(max(dataY[:,4]))
print(min_y,max_y)

179.0 748.0


In [8]:
#INFO: valores min max de la X
min_x=(float)(min(dataY[:,3]))
max_x=(float)(max(dataY[:,3]))
print(min_x,max_x)

10.0 375.0


In [9]:
#Esta función obtiene la media de un cojunto de señales RSSI (normalizada)
def getAVG(vs):
    if (len(vs)==0):
        return 0
    #print(" avg:", vs)
    return (np.mean(vs)-min_v)/(max_v-min_v)

#Esta función obtiene el MAX de un cojunto de señales RSSI (normalizada)
def getMAX(vs):
    if (len(vs)==0):
        return 0
    #print(" avg:", vs)
    return (max(vs)-min_v)/(max_v-min_v)

#Esta función obtiene el MIN de un cojunto de señales RSSI (normalizada)
def getMIN(vs):
    if (len(vs)==0):
        return 0
    #print(" avg:", vs)
    return (min(vs)-min_v)/(max_v-min_v)

In [10]:
#Valores de X, Y
X=[]
Y=[]



c=0

#Desde el tiempo inicial al final (en segundos) de uno en uno (con un desplazamiento en funcion del tamaño de ventana para recoger datos anteriores y futuros)
for t in np.arange(min_t-min(tW1),max_t,1.0):
    print(t)
    
    #Recogemos la posicioón de X,Y más cercana anterior y posterior a este tiempo t
    agXY0=dataY[np.sort(np.where( (dataY[:,0] <  t)))][0][-1]
    agXYNn=dataY[np.sort(np.where( (dataY[:,0] >=  t)))][0][0]
    #calculamos el incremento de tiempo respecto t, del futuro y del pasado
    incT0=t-agXY0[0]
    incTN=agXYNn[0]-t
    print("agXY0:",agXY0, "incT0:",incT0)
    print("agXYNn:",agXYNn, "incTN:",incTN)
    
    #IMPORTANTE: si el usuario no etiquetó esa muestra en un tiempo cercano (a 10 segundos), la descartamos!
    if(incT0>5 or incTN> 5):
        print("NOT DATA AVAILABLE!")
        continue
    
    #valores de las x-> NO posicion, los datos de entrada de RSSI
    xi=[]
    for a in anchors:
        xirssi1=[]
        xirssi2=[]
        xirssi3=[]
        xirssi4=[]
        xirssi5=[]
        xirssi6=[]
        #Ventanas pasadas
        for it in range(len(tW1)-2,-1,-1):
            t0=t+tW1[it]
            tN=t+tW1[it+1]
             #Todos los datos en ese segmento de ventana
            ag1=data[np.where((data[:,2] == a) & (data[:,0] <= t0) & (data[:,0] >=  tN))]
            #print("t+:",t,"a:",str(a),"t0:",t0,"tN:",tN," ag1:", ag1)
            #Sacamos las 3 características de esa ventana (max,min,media)
            xirssi1.append(getAVG(ag1[:,3]))
            xirssi2.append(getMAX(ag1[:,3]))
            xirssi3.append(getMIN(ag1[:,3]))

            
        #añadimos los valores de entradas futuras y pasadas a la sequencia     
        xi.append(xirssi1)
        xi.append(xirssi2)
        xi.append(xirssi3)

    

    
    #calculamos una posición X,Y de la imagen ponderada respecto las posiciones más cercana anterior y posterior a este tiempo t
    w0= 1-(incT0)/(incT0+incTN)
    wn= 1-(incTN)/(incT0+incTN)
    
    posX=(agXYNn[3]*wn+agXY0[3]*w0)
    posY=(agXYNn[4]*wn+agXY0[4]*w0)
    print("posX:",posX, "posY:",posY)
    
    #normalizamos 
    posX=(posX-min_x)/(max_x-min_x)
    posY=(posY-min_y)/(max_y-min_y)
    print("posX:",posX, "posY:",posY)
    
    #añadimos la sequencia de caracteristicas X (RSSI) e Y(posX,posY de la imagen)
    X.append(np.transpose(xi))
    Y.append([posX,posY])
    

    
    
    print("count:",c)



    c=c+1
    if(c>5000):
        break
        
        
#Importante: pasar los datos a NUMPY para trabajar con el modelo de DL
X=np.array(X)
Y=np.array(Y)
print(X.shape)
print(Y.shape)


1662734476.0
agXY0: [1662734467 '2022-09-09 16:41:07' 1662734467 124 444] incT0: 9.0
agXYNn: [1662734479 '2022-09-09 16:41:19' 1662734479 115 451] incTN: 3.0
NOT DATA AVAILABLE!
1662734477.0
agXY0: [1662734467 '2022-09-09 16:41:07' 1662734467 124 444] incT0: 10.0
agXYNn: [1662734479 '2022-09-09 16:41:19' 1662734479 115 451] incTN: 2.0
NOT DATA AVAILABLE!
1662734478.0
agXY0: [1662734467 '2022-09-09 16:41:07' 1662734467 124 444] incT0: 11.0
agXYNn: [1662734479 '2022-09-09 16:41:19' 1662734479 115 451] incTN: 1.0
NOT DATA AVAILABLE!
1662734479.0
agXY0: [1662734467 '2022-09-09 16:41:07' 1662734467 124 444] incT0: 12.0
agXYNn: [1662734479 '2022-09-09 16:41:19' 1662734479 115 451] incTN: 0.0
NOT DATA AVAILABLE!
1662734480.0
agXY0: [1662734479 '2022-09-09 16:41:19' 1662734479 115 451] incT0: 1.0
agXYNn: [1662734480 '2022-09-09 16:41:20' 1662734480 112 464] incTN: 0.0
posX: 112.0 posY: 464.0
posX: 0.27945205479452057 posY: 0.5008787346221442
count: 0
1662734481.0
agXY0: [1662734480 '2022-09-09

agXY0: [1662734745 '2022-09-09 16:45:45' 1662734745 303 651] incT0: 2.0
agXYNn: [1662734747 '2022-09-09 16:45:47' 1662734747 278 643] incTN: 0.0
posX: 278.0 posY: 643.0
posX: 0.7342465753424657 posY: 0.8154657293497364
count: 217
1662734748.0
agXY0: [1662734747 '2022-09-09 16:45:47' 1662734747 278 643] incT0: 1.0
agXYNn: [1662734750 '2022-09-09 16:45:50' 1662734750 262 643] incTN: 2.0
posX: 272.6666666666667 posY: 643.0000000000001
posX: 0.719634703196347 posY: 0.8154657293497366
count: 218
1662734749.0
agXY0: [1662734747 '2022-09-09 16:45:47' 1662734747 278 643] incT0: 2.0
agXYNn: [1662734750 '2022-09-09 16:45:50' 1662734750 262 643] incTN: 1.0
posX: 267.33333333333337 posY: 643.0000000000001
posX: 0.7050228310502284 posY: 0.8154657293497366
count: 219
1662734750.0
agXY0: [1662734747 '2022-09-09 16:45:47' 1662734747 278 643] incT0: 3.0
agXYNn: [1662734750 '2022-09-09 16:45:50' 1662734750 262 643] incTN: 0.0
posX: 262.0 posY: 643.0
posX: 0.6904109589041096 posY: 0.8154657293497364
coun

agXY0: [1662734782 '2022-09-09 16:46:22' 1662734782 333 347] incT0: 1.0
agXYNn: [1662734783 '2022-09-09 16:46:23' 1662734783 333 347] incTN: 0.0
posX: 333.0 posY: 347.0
posX: 0.8849315068493151 posY: 0.29525483304042177
count: 253
1662734784.0
agXY0: [1662734783 '2022-09-09 16:46:23' 1662734783 333 347] incT0: 1.0
agXYNn: [1662734785 '2022-09-09 16:46:25' 1662734785 333 368] incTN: 1.0
posX: 333.0 posY: 357.5
posX: 0.8849315068493151 posY: 0.31370826010544817
count: 254
1662734785.0
agXY0: [1662734783 '2022-09-09 16:46:23' 1662734783 333 347] incT0: 2.0
agXYNn: [1662734785 '2022-09-09 16:46:25' 1662734785 333 368] incTN: 0.0
posX: 333.0 posY: 368.0
posX: 0.8849315068493151 posY: 0.3321616871704745
count: 255
1662734786.0
agXY0: [1662734785 '2022-09-09 16:46:25' 1662734785 333 368] incT0: 1.0
agXYNn: [1662734786 '2022-09-09 16:46:26' 1662734786 333 419] incTN: 0.0
posX: 333.0 posY: 419.0
posX: 0.8849315068493151 posY: 0.421792618629174
count: 256
1662734787.0
agXY0: [1662734786 '2022-09

posX: 128.0 posY: 484.0
posX: 0.3232876712328767 posY: 0.5360281195079086
count: 293
1662734824.0
agXY0: [1662734823 '2022-09-09 16:47:03' 1662734823 128 484] incT0: 1.0
agXYNn: [1662734824 '2022-09-09 16:47:04' 1662734824 128 473] incTN: 0.0
posX: 128.0 posY: 473.0
posX: 0.3232876712328767 posY: 0.5166959578207382
count: 294
1662734825.0
agXY0: [1662734824 '2022-09-09 16:47:04' 1662734824 128 473] incT0: 1.0
agXYNn: [1662734826 '2022-09-09 16:47:06' 1662734826 104 481] incTN: 1.0
posX: 116.0 posY: 477.0
posX: 0.29041095890410956 posY: 0.523725834797891
count: 295
1662734826.0
agXY0: [1662734824 '2022-09-09 16:47:04' 1662734824 128 473] incT0: 2.0
agXYNn: [1662734826 '2022-09-09 16:47:06' 1662734826 104 481] incTN: 0.0
posX: 104.0 posY: 481.0
posX: 0.25753424657534246 posY: 0.5307557117750439
count: 296
1662734827.0
agXY0: [1662734826 '2022-09-09 16:47:06' 1662734826 98 498] incT0: 1.0
agXYNn: [1662734828 '2022-09-09 16:47:08' 1662734828 95 522] incTN: 1.0
posX: 96.5 posY: 510.0
posX: 

agXY0: [1662734838 '2022-09-09 16:47:18' 1662734838 147 613] incT0: 59.0
agXYNn: [1662735033 '2022-09-09 16:50:33' 1662735033 150 617] incTN: 136.0
NOT DATA AVAILABLE!
1662734898.0
agXY0: [1662734838 '2022-09-09 16:47:18' 1662734838 147 613] incT0: 60.0
agXYNn: [1662735033 '2022-09-09 16:50:33' 1662735033 150 617] incTN: 135.0
NOT DATA AVAILABLE!
1662734899.0
agXY0: [1662734838 '2022-09-09 16:47:18' 1662734838 147 613] incT0: 61.0
agXYNn: [1662735033 '2022-09-09 16:50:33' 1662735033 150 617] incTN: 134.0
NOT DATA AVAILABLE!
1662734900.0
agXY0: [1662734838 '2022-09-09 16:47:18' 1662734838 147 613] incT0: 62.0
agXYNn: [1662735033 '2022-09-09 16:50:33' 1662735033 150 617] incTN: 133.0
NOT DATA AVAILABLE!
1662734901.0
agXY0: [1662734838 '2022-09-09 16:47:18' 1662734838 147 613] incT0: 63.0
agXYNn: [1662735033 '2022-09-09 16:50:33' 1662735033 150 617] incTN: 132.0
NOT DATA AVAILABLE!
1662734902.0
agXY0: [1662734838 '2022-09-09 16:47:18' 1662734838 147 613] incT0: 64.0
agXYNn: [1662735033 '2

...

posX: 77.0 posY: 346.0
posX: 0.18356164383561643 posY: 0.29349736379613356
count: 2783
1662740300.0
agXY0: [1662740299 '2022-09-09 18:18:19' 1662740299 77 346] incT0: 1.0
agXYNn: [1662740300 '2022-09-09 18:18:20' 1662740300 77 355] incTN: 0.0
posX: 77.0 posY: 355.0
posX: 0.18356164383561643 posY: 0.3093145869947276
count: 2784
1662740301.0
agXY0: [1662740300 '2022-09-09 18:18:20' 1662740300 82 373] incT0: 1.0
agXYNn: [1662740301 '2022-09-09 18:18:21' 1662740301 112 427] incTN: 0.0
posX: 112.0 posY: 427.0
posX: 0.27945205479452057 posY: 0.4358523725834798
count: 2785
1662740302.0
agXY0: [1662740301 '2022-09-09 18:18:21' 1662740301 112 427] incT0: 1.0
agXYNn: [1662740304 '2022-09-09 18:18:24' 1662740304 113 439] incTN: 2.0
posX: 112.33333333333334 posY: 431.0
posX: 0.280365296803653 posY: 0.4428822495606327
count: 2786
1662740303.0
agXY0: [1662740301 '2022-09-09 18:18:21' 1662740301 112 427] incT0: 2.0
agXYNn: [1662740304 '2022-09-09 18:18:24' 1662740304 113 439] incTN: 1.0
posX: 112.666

posX: 110.0 posY: 447.0
posX: 0.273972602739726 posY: 0.4710017574692443
count: 2818
1662740345.0
agXY0: [1662740344 '2022-09-09 18:19:04' 1662740344 103 440] incT0: 1.0
agXYNn: [1662740345 '2022-09-09 18:19:05' 1662740345 95 425] incTN: 0.0
posX: 95.0 posY: 425.0
posX: 0.2328767123287671 posY: 0.43233743409490333
count: 2819
1662740346.0
agXY0: [1662740345 '2022-09-09 18:19:05' 1662740345 95 425] incT0: 1.0
agXYNn: [1662740346 '2022-09-09 18:19:06' 1662740346 95 413] incTN: 0.0
posX: 95.0 posY: 413.0
posX: 0.2328767123287671 posY: 0.4112478031634446
count: 2820
1662740347.0
agXY0: [1662740346 '2022-09-09 18:19:06' 1662740346 96 396] incT0: 1.0
agXYNn: [1662740347 '2022-09-09 18:19:07' 1662740347 98 370] incTN: 0.0
posX: 98.0 posY: 370.0
posX: 0.2410958904109589 posY: 0.335676625659051
count: 2821
1662740348.0
agXY0: [1662740347 '2022-09-09 18:19:07' 1662740347 98 355] incT0: 1.0
agXYNn: [1662740348 '2022-09-09 18:19:08' 1662740348 98 340] incTN: 0.0
posX: 98.0 posY: 340.0
posX: 0.2410

posX: 281.6666666666667 posY: 593.0000000000001
posX: 0.7442922374429224 posY: 0.7275922671353253
count: 2854
1662740381.0
agXY0: [1662740378 '2022-09-09 18:19:38' 1662740378 279 585] incT0: 3.0
agXYNn: [1662740381 '2022-09-09 18:19:41' 1662740381 283 597] incTN: 0.0
posX: 283.0 posY: 597.0
posX: 0.7479452054794521 posY: 0.7346221441124781
count: 2855
1662740382.0
agXY0: [1662740381 '2022-09-09 18:19:41' 1662740381 284 597] incT0: 1.0
agXYNn: [1662740382 '2022-09-09 18:19:42' 1662740382 290 595] incTN: 0.0
posX: 290.0 posY: 595.0
posX: 0.7671232876712328 posY: 0.7311072056239016
count: 2856
1662740383.0
agXY0: [1662740382 '2022-09-09 18:19:42' 1662740382 310 593] incT0: 1.0
agXYNn: [1662740383 '2022-09-09 18:19:43' 1662740383 314 593] incTN: 0.0
posX: 314.0 posY: 593.0
posX: 0.8328767123287671 posY: 0.7275922671353251
count: 2857
1662740384.0
agXY0: [1662740383 '2022-09-09 18:19:43' 1662740383 321 593] incT0: 1.0
agXYNn: [1662740384 '2022-09-09 18:19:44' 1662740384 336 602] incTN: 0.0


posX: 184.0 posY: 281.0
posX: 0.4767123287671233 posY: 0.17926186291739896
count: 2891
1662740418.0
agXY0: [1662740417 '2022-09-09 18:20:17' 1662740417 184 281] incT0: 1.0
agXYNn: [1662740418 '2022-09-09 18:20:18' 1662740418 184 277] incTN: 0.0
posX: 184.0 posY: 277.0
posX: 0.4767123287671233 posY: 0.17223198594024605
count: 2892
1662740419.0
agXY0: [1662740418 '2022-09-09 18:20:18' 1662740418 184 277] incT0: 1.0
agXYNn: [1662740419 '2022-09-09 18:20:19' 1662740419 202 282] incTN: 0.0
posX: 202.0 posY: 282.0
posX: 0.5260273972602739 posY: 0.18101933216168717
count: 2893
1662740420.0
agXY0: [1662740419 '2022-09-09 18:20:19' 1662740419 258 312] incT0: 1.0
agXYNn: [1662740420 '2022-09-09 18:20:20' 1662740420 272 338] incTN: 0.0
posX: 272.0 posY: 338.0
posX: 0.7178082191780822 posY: 0.27943760984182775
count: 2894
1662740421.0
agXY0: [1662740420 '2022-09-09 18:20:20' 1662740420 274 346] incT0: 1.0
agXYNn: [1662740421 '2022-09-09 18:20:21' 1662740421 274 373] incTN: 0.0
posX: 274.0 posY: 37

posX: 246.0 posY: 377.0
posX: 0.6465753424657534 posY: 0.34797891036906853
count: 2926
1662740453.0
agXY0: [1662740452 '2022-09-09 18:20:52' 1662740452 246 377] incT0: 1.0
agXYNn: [1662740453 '2022-09-09 18:20:53' 1662740453 249 381] incTN: 0.0
posX: 249.0 posY: 381.0
posX: 0.6547945205479452 posY: 0.35500878734622143
count: 2927
1662740454.0
agXY0: [1662740453 '2022-09-09 18:20:53' 1662740453 250 399] incT0: 1.0
agXYNn: [1662740454 '2022-09-09 18:20:54' 1662740454 254 409] incTN: 0.0
posX: 254.0 posY: 409.0
posX: 0.6684931506849315 posY: 0.40421792618629176
count: 2928
1662740455.0
agXY0: [1662740454 '2022-09-09 18:20:54' 1662740454 254 409] incT0: 1.0
agXYNn: [1662740455 '2022-09-09 18:20:55' 1662740455 256 410] incTN: 0.0
posX: 256.0 posY: 410.0
posX: 0.673972602739726 posY: 0.40597539543058
count: 2929
1662740456.0
agXY0: [1662740455 '2022-09-09 18:20:55' 1662740455 256 413] incT0: 1.0
agXYNn: [1662740456 '2022-09-09 18:20:56' 1662740456 255 415] incTN: 0.0
posX: 255.0 posY: 415.0


In [11]:
print(X)
print(X.shape)


[[[0.92757142 0.93736344 0.91964069 ... 0.95120175 0.9538723  0.94804564]
  [0.92020717 0.93736344 0.90604516 ... 0.93930566 0.9538723  0.92571012]
  [0.92409161 0.92983734 0.91721292 ... 0.93461196 0.94658898 0.92571012]
  ...
  [0.89924739 0.91405681 0.88443797 ... 0.89633406 0.93663511 0.85603302]
  [0.88468075 0.88492353 0.88443797 ... 0.84195193 0.85603302 0.82787084]
  [0.86210245 0.88492353 0.83928138 ... 0.8272639  0.82787084 0.82665696]]

 [[0.92303957 0.93736344 0.90604516 ... 0.94796472 0.9538723  0.93833455]
  [0.91769847 0.92983734 0.90604516 ... 0.93186048 0.93833455 0.92571012]
  [0.92530549 0.92983734 0.92085458 ... 0.93606863 0.94658898 0.93008012]
  ...
  [0.88468075 0.88492353 0.88443797 ... 0.84195193 0.85603302 0.82787084]
  [0.86210245 0.88492353 0.83928138 ... 0.8272639  0.82787084 0.82665696]
  [0.81063365 0.83928138 0.78198592 ... 0.75333819 0.82665696 0.68001942]]

 [[0.92020717 0.93736344 0.90604516 ... 0.93930566 0.9538723  0.92571012]
  [0.92409161 0.929837

In [12]:
print(Y)
print(Y.shape)


[[0.27945205 0.50087873]
 [0.24931507 0.53602812]
 [0.21643836 0.5711775 ]
 ...
 [0.67671233 0.59929701]
 [0.65753425 0.55272408]
 [0.63835616 0.50615114]]
(2942, 2)


In [ ]:
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.layers import MaxPooling2D, Activation, Dense, Input, Conv1D, Conv2D, ReLU, BatchNormalization, Add, AveragePooling2D, Flatten, Dropout, LSTM, TimeDistributed, MaxPooling1D, Attention
from tensorflow.keras.models import Model
from sklearn.model_selection import KFold
import tensorflow as tf
import numpy as np

# Dividimos los datos en K fold para cross validation
kf = KFold(n_splits=10, shuffle=True)
kf.get_n_splits(X)

# Un fichero para escribir los resultados de predicción y reales ("borramos lo anterior")
with open(flat + "xy.tsv", "w") as f:
    f.write("")

# Para cada K del cross validator
for train_index, test_index in kf.split(X):
    # Datos de train y test
    print("TRAIN:", train_index, "TEST:", test_index)
    x_train, x_val = X[train_index], X[test_index]
    y_train, y_val = Y[train_index], Y[test_index]

    # Crear un dataset para train y validación
    train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(64)
    val_dataset = tf.data.Dataset.from_tensor_slices((x_val, y_val)).batch(64)

    # Un nuevo modelo
    inputs = Input(shape=(X.shape[1], X.shape[2]))

    # 3 capas de convolución 
    x = Conv1D(filters=16, kernel_size=2, activation='relu')(inputs)
    x = Conv1D(filters=32, kernel_size=3, activation='relu')(x)
    x = Conv1D(filters=64, kernel_size=3, activation='relu')(x)

    # 2 capas de LSTM de secuencia
    x = Dropout(0.5)(x)
    x = LSTM(32, return_sequences=True)(x)
    x = Dropout(0.5)(x)
    lstm_out = LSTM(32, return_sequences=True)(x)

    # Capa de atención
    attention_out = Attention()([lstm_out, lstm_out])

    # Aplanamos los datos y pasamos a una capa densa
    x = Flatten()(attention_out)
    x = Dense(512)(x)
    x = Dense(256)(x)
    outputs = Dense(2, activation="sigmoid")(x)

    model = Model(inputs, outputs)

    model.compile(loss='mean_squared_error', optimizer='adam')
    model.summary()

    # Iteramos 1000 veces
    history = model.fit(train_dataset,
                        validation_data=val_dataset,
                        epochs=1000)
    
    # Predecimos
    yhat = model.predict(x_val)

    # Desnormalizamos 
    x1 = y_val[:, 0] * (max_x - min_x) + min_x
    y1 = y_val[:, 1] * (max_y - min_y) + min_y
    x2 = yhat[:, 0] * (max_x - min_x) + min_x
    y2 = yhat[:, 1] * (max_y - min_y) + min_y

    # Calculamos error absoluto y ponemos índice, posiciones reales y predichas 
    absx = 0.0
    absy = 0.0

    with open(flat + "xy.tsv", "a") as f:
        for i in range(len(x2)):
            f.write(f"{test_index[i]}\t{x1[i]}\t{y1[i]}\t{x2[i]}\t{y2[i]}\n")
            absx += abs(x1[i] - x2[i])
            absy += abs(y1[i] - y2[i])

    absx /= len(x2)
    absy /= len(x2)

    print("absx:", absx)
    print("absy:", absy)


TRAIN: [   0    1    2 ... 2939 2940 2941] TEST: [  17   19   25   39   53   69   83   85   89   99  109  121  135  137
  144  150  155  158  159  182  189  191  216  217  232  245  248  259
  261  284  288  306  307  308  332  337  338  358  361  365  368  372
  399  400  401  413  416  429  458  464  471  478  490  493  512  523
  525  530  547  551  553  570  589  591  610  612  627  652  670  671
  673  679  680  708  709  731  743  744  746  749  759  760  766  790
  799  808  841  842  847  852  863  868  871  873  874  877  928  941
  953  959  965  972  974 1003 1022 1029 1071 1073 1093 1111 1125 1146
 1149 1164 1166 1169 1175 1183 1195 1224 1231 1237 1240 1243 1258 1259
 1288 1289 1300 1311 1322 1343 1351 1358 1361 1369 1380 1390 1395 1401
 1418 1421 1434 1446 1450 1459 1462 1476 1487 1506 1519 1525 1530 1548
 1569 1579 1586 1593 1596 1622 1639 1640 1653 1661 1675 1688 1697 1702
 1705 1708 1719 1736 1753 1761 1771 1777 1780 1785 1787 1788 1807 1809
 1817 1826 1865 1881 1884 18

42/42 [==============================] - 0s 5ms/step - loss: 0.0180 - val_loss: 0.0150
Epoch 28/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0174 - val_loss: 0.0154
Epoch 29/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0174 - val_loss: 0.0195
Epoch 30/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0173 - val_loss: 0.0165
Epoch 31/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0174 - val_loss: 0.0175
Epoch 32/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0178 - val_loss: 0.0166
Epoch 33/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0173 - val_loss: 0.0150
Epoch 34/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0163 - val_loss: 0.0149
Epoch 35/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0161 - val_loss: 0.0146
Epoch 36/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0162 - val_loss: 0.0163
Epoc

42/42 [==============================] - 0s 5ms/step - loss: 0.0117 - val_loss: 0.0134
Epoch 109/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0124 - val_loss: 0.0123
Epoch 110/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0116 - val_loss: 0.0107
Epoch 111/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0112 - val_loss: 0.0109
Epoch 112/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0113 - val_loss: 0.0107
Epoch 113/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0111 - val_loss: 0.0106
Epoch 114/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0112 - val_loss: 0.0104
Epoch 115/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0111 - val_loss: 0.0121
Epoch 116/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0116 - val_loss: 0.0104
Epoch 117/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0107 - val_loss: 0.

42/42 [==============================] - 0s 5ms/step - loss: 0.0089 - val_loss: 0.0085
Epoch 189/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0093 - val_loss: 0.0085
Epoch 190/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0087 - val_loss: 0.0087
Epoch 191/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0088 - val_loss: 0.0087
Epoch 192/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0089 - val_loss: 0.0085
Epoch 193/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0086 - val_loss: 0.0095
Epoch 194/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0091 - val_loss: 0.0084
Epoch 195/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0092 - val_loss: 0.0093
Epoch 196/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0093 - val_loss: 0.0112
Epoch 197/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0093 - val_loss: 0.

42/42 [==============================] - 0s 6ms/step - loss: 0.0079 - val_loss: 0.0074
Epoch 269/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0077 - val_loss: 0.0082
Epoch 270/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0077 - val_loss: 0.0084
Epoch 271/1000
42/42 [==============================] - 0s 6ms/step - loss: 0.0078 - val_loss: 0.0081
Epoch 272/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0081 - val_loss: 0.0092
Epoch 273/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0080 - val_loss: 0.0076
Epoch 274/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0078 - val_loss: 0.0075
Epoch 275/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0073 - val_loss: 0.0076
Epoch 276/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0078 - val_loss: 0.0075
Epoch 277/1000
42/42 [==============================] - 0s 5ms/step - loss: 0.0074 - val_loss: 0.

...

42/42 [==============================] - 0s 10ms/step - loss: 0.0060 - val_loss: 0.0064
Epoch 922/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0049 - val_loss: 0.0060
Epoch 923/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0051 - val_loss: 0.0056
Epoch 924/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0048 - val_loss: 0.0050
Epoch 925/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0047 - val_loss: 0.0054
Epoch 926/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0048 - val_loss: 0.0052
Epoch 927/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0045 - val_loss: 0.0052
Epoch 928/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0046 - val_loss: 0.0049
Epoch 929/1000
42/42 [==============================] - 0s 9ms/step - loss: 0.0049 - val_loss: 0.0059
Epoch 930/1000
42/42 [==============================] - 0s 10ms/step - loss: 0.0057 - val

10/10 [==============================] - 0s 3ms/step
absx:21.597768771953476
absy:29.93278601386611
TRAIN: [   0    1    2 ... 2939 2940 2941] TEST: [   4   14   15   27   40   65   67   87   97  110  116  121  150  153
  154  180  194  212  219  225  237  249  255  259  265  266  293  295
  320  322  329  336  339  341  353  355  356  368  376  393  394  395
  397  403  409  432  441  459  462  467  480  484  486  521  534  535
  557  575  593  607  614  616  617  626  642  663  671  696  702  706
  710  712  713  715  718  738  744  746  762  773  788  809  810  819
  822  842  848  849  864  875  883  892  894  923  925  938  947  958
  969  970  972  979  982  986 1000 1021 1030 1036 1040 1062 1073 1076
 1079 1086 1092 1101 1104 1140 1142 1174 1192 1193 1194 1212 1213 1229
 1230 1231 1236 1265 1292 1298 1300 1307 1320 1325 1335 1345 1353 1356
 1357 1376 1378 1385 1391 1417 1427 1455 1458 1466 1469 1483 1506 1516
 1519 1533 1537 1552 1574 1588 1590 1593 1595 1615 1617 1624 1630 1655

42/42 [==============================] - 1s 15ms/step - loss: 0.0177 - val_loss: 0.0148
Epoch 33/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0171 - val_loss: 0.0141
Epoch 34/1000
42/42 [==============================] - 1s 16ms/step - loss: 0.0171 - val_loss: 0.0151
Epoch 35/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0170 - val_loss: 0.0139
Epoch 36/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0173 - val_loss: 0.0145
Epoch 37/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0171 - val_loss: 0.0159
Epoch 38/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0162 - val_loss: 0.0139
Epoch 39/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0164 - val_loss: 0.0141
Epoch 40/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0169 - val_loss: 0.0145
Epoch 41/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0161 - val_loss: 0

42/42 [==============================] - 1s 14ms/step - loss: 0.0109 - val_loss: 0.0099
Epoch 113/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0114 - val_loss: 0.0107
Epoch 114/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0111 - val_loss: 0.0099
Epoch 115/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0109 - val_loss: 0.0101
Epoch 116/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0110 - val_loss: 0.0102
Epoch 117/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0116 - val_loss: 0.0101
Epoch 118/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0110 - val_loss: 0.0103
Epoch 119/1000
42/42 [==============================] - 1s 14ms/step - loss: 0.0111 - val_loss: 0.0099
Epoch 120/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0106 - val_loss: 0.0096
Epoch 121/1000
42/42 [==============================] - 1s 15ms/step - loss: 0.0107 - va

42/42 [==============================] - 1s 21ms/step - loss: 0.0092 - val_loss: 0.0085
Epoch 192/1000
42/42 [==============================] - 1s 21ms/step - loss: 0.0095 - val_loss: 0.0100
Epoch 193/1000
42/42 [==============================] - 1s 27ms/step - loss: 0.0090 - val_loss: 0.0088
Epoch 194/1000
42/42 [==============================] - 1s 24ms/step - loss: 0.0090 - val_loss: 0.0084
Epoch 195/1000
42/42 [==============================] - 1s 28ms/step - loss: 0.0089 - val_loss: 0.0090
Epoch 196/1000
42/42 [==============================] - 1s 26ms/step - loss: 0.0087 - val_loss: 0.0087
Epoch 197/1000
42/42 [==============================] - 1s 29ms/step - loss: 0.0086 - val_loss: 0.0091
Epoch 198/1000
42/42 [==============================] - 1s 25ms/step - loss: 0.0096 - val_loss: 0.0089
Epoch 199/1000
42/42 [==============================] - 1s 24ms/step - loss: 0.0090 - val_loss: 0.0084
Epoch 200/1000
42/42 [==============================] - 1s 24ms/step - loss: 0.0089 - va